# Understanding the Kiva Dataset

Before we actually get into the work of predicting anything based on the data Kiva makes public, we first want to get a better picture of what the dataset actually looks like.

Our first step: What is the schema of the data? Spark SQL will make it easy to query data in the future, but we need to know first what is available.

In [1]:
sparkSql = (SparkSession.builder
         .master("local")
         .appName("Kiva Exploration")
         .getOrCreate())

loans = sparkSql.read.format('json').load('kiva-data/loans.json')
loans.registerTempTable('loans')
lenders = sparkSql.read.format('json').load('kiva-data/lenders.json')
lenders.registerTempTable('lenders')
loans_lenders = sparkSql.read.format('json').load('kiva-data/loans_lenders.json')
loans_lenders.registerTempTable('loans_lenders')

In [2]:
loans.printSchema()

root
 |-- activity: string (nullable = true)
 |-- basket_amount: long (nullable = true)
 |-- bonus_credit_eligibility: boolean (nullable = true)
 |-- borrowers: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- first_name: string (nullable = true)
 |    |    |-- gender: string (nullable = true)
 |    |    |-- last_name: string (nullable = true)
 |    |    |-- pictured: boolean (nullable = true)
 |-- currency_exchange_loss_amount: double (nullable = true)
 |-- delinquent: boolean (nullable = true)
 |-- description: struct (nullable = true)
 |    |-- languages: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- texts: struct (nullable = true)
 |    |    |-- ar: string (nullable = true)
 |    |    |-- en: string (nullable = true)
 |    |    |-- es: string (nullable = true)
 |    |    |-- fr: string (nullable = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- mn: string (nullable = true)
 |    |    |--

In [3]:
loans.groupby(loans.status).count().collect()

[Row(status=u'refunded', count=5504),
 Row(status=u'defaulted', count=21776),
 Row(status=u'in_repayment', count=155749),
 Row(status=u'reviewed', count=3),
 Row(status=u'deleted', count=2721),
 Row(status=u'paid', count=775330),
 Row(status=u'issue', count=199),
 Row(status=u'inactive_expired', count=12421),
 Row(status=u'fundraising', count=3986),
 Row(status=u'expired', count=33773),
 Row(status=u'inactive', count=2493),
 Row(status=u'funded', count=173),
 Row(status=u'', count=2)]

In [4]:
loans.groupby(loans.delinquent).count().collect()

[Row(delinquent=None, count=970465), Row(delinquent=True, count=43665)]

In [6]:
loans.where(loans.delinquent == True).groupby(loans.status).count().collect()

[Row(status=u'refunded', count=156),
 Row(status=u'defaulted', count=20116),
 Row(status=u'in_repayment', count=23393)]

In [4]:
bad_pct_df = sparkSql.sql('''
SELECT
    sub.country,
    sub.bad_loans / sub.total_loans * 100.0 as bad_loan_pct
FROM (SELECT
        SUM(CASE WHEN
            loans.status = 'refunded' OR
            loans.status = 'expired' OR
            loans.status = 'defaulted' OR
            loans.delinquent = True
        THEN 1
        ELSE 0 END) AS bad_loans,
        COUNT(*) AS total_loans,
        loans.location.country
    FROM loans
    GROUP BY
    loans.location.country
) sub
''').toPandas()

bad_pct_df

country  bad_loan_pct
0                     Chad     93.220339
1                 Paraguay      2.893067
2                    Yemen     24.980195
3                  Senegal      7.014218
4              Philippines      2.515182
5                   Turkey      0.233645
6                   Malawi     13.125000
7                     Iraq     35.476593
8                 Cambodia      1.433968
9              Afghanistan     26.235741
10                  Rwanda      6.648555
11                  Jordan     16.066482
12                  Kosovo     11.893370
13               Sri Lanka     25.296443
14                    Togo     16.013720
15                 Ecuador      7.329710
16                 Lesotho      4.081633
17                 Albania      9.304468
18              Madagascar      3.710247
19               Nicaragua     10.434992
20                   Ghana      9.171567
21            Sierra Leone     21.054804
22                    Peru      4.051516
23                   Benin      8.137597
24                   India      4.391382
25           United States     34.945144
26                   China      0.000000
27             Timor-Leste      9.585492
28                 Lao PDR      0.000000
29                 Somalia     17.316017
..                     ...           ...
62              Kyrgyzstan      7.112293
63                   Samoa      3.421662
64              Mozambique     10.196484
65                  Brazil     42.477876
66                  Belize     45.026178
67                   Kenya     12.214316
68                 Lebanon      6.509946
69      Dominican Republic     14.982415
70                Tanzania     11.312424
71                Botswana    100.000000
72  Bosnia and Herzegovina      5.536913
73                   Haiti     25.527192
74                Cameroon      4.695009
75        Papua New Guinea      0.000000
76         Solomon Islands      0.000000
77                Bulgaria      2.333333
78              St Vincent     72.727273
79                   Nepal      0.397953
80             El Salvador     17.143167
81                   Egypt      0.000000
82              Costa Rica      8.917357
83            Congo (Rep.)      1.198257
84            Burkina Faso      2.172702
85            South Africa      3.364486
86                Colombia     21.693634
87                Pakistan      6.085563
88                 Vanuatu      0.000000
89                 Moldova      8.549223
90                 Vietnam      5.473769
91                    Mali     10.650330

[92 rows x 2 columns]

In [8]:
bad_pct_df.sort_values(by='bad_loan_pct', ascending=False).head()

country  bad_loan_pct
71    Botswana    100.000000
47        Gaza    100.000000
0         Chad     93.220339
78  St Vincent     72.727273
66      Belize     45.026178

In [9]:
bad_pct_df.sort_values(by='bad_loan_pct').head()

country  bad_loan_pct
26       China             0
41  Cape Verde             0
39    Thailand             0
38  Bangladesh             0
37  Mauritania             0